# Codierung und Blockzerlegung

In [51]:
import doctest

In [52]:
def codierungZeichen(zeichen, abc):
    """ 
    >>> codierungZeichen('A', ' ABCDEFGHIJKLMNOPQRSTUVWXYZ')
    1
    """
    return abc.index(zeichen)

def decodierungZahl(zahl, abc):
    """ 
    >>> decodierungZahl(1, ' ABCDEFGHIJKLMNOPQRSTUVWXYZ')
    'A'
    """
    return abc[zahl]
doctest.run_docstring_examples(codierungZeichen, globals())


In [53]:
def zerlegung(wort, blocklaenge):
    """ 
    >>> zerlegung('TEST', 2)
    ['TE', 'ST']
    >>> zerlegung('HALLO', 3)
    ['HAL', 'LO ']
    >>> zerlegung('HALLO', 2)
    ['HA', 'LL', 'O ']
    >>> zerlegung('', 4)
    []
    """
    liste = []
    block = ''
    for c in wort:
        if len(block) == blocklaenge:
            liste = liste + [block]
            block = ''
        block = block + c
    # Falls letzter Block nicht voll ist
    if block != '':
        fehlend = blocklaenge - len(block)
        block = block + fehlend * ' '
        liste = liste + [block]
    return liste
doctest.run_docstring_examples(zerlegung, globals())

In [54]:
def codierungBlock(wort, abc):
    """ 
    >>> codierungBlock('BAD', ' ABCDEFGHIJKLMNOPQRSTUVWXYZ')
    20104
   
    >>> codierungBlock('O ', ' ABCDEFGHIJKLMNOPQRSTUVWXYZ')
    1500
    """
    hilfszahl = 0
    for c in wort:
        hilfszahl = hilfszahl*100 + codierungZeichen(c, abc)
    return hilfszahl



In [55]:
def codierungBlockListe(blockListe, abc):
    """ 
    >>> codierungBlockListe(['HA', 'LL', 'O '], ' ABCDEFGHIJKLMNOPQRSTUVWXYZ')
    [801, 1212, 1500]
    """
    liste = []
    for block in blockListe:
        liste = liste + [codierungBlock(block, abc)]
    return liste
doctest.run_docstring_examples(codierungBlock, globals())
doctest.run_docstring_examples(codierungBlockListe, globals())

In [56]:
def codierung(wort, blocklaenge, abc):
    """ 
    >>> codierung('HALLO', 2, ' ABCDEFGHIJKLMNOPQRSTUVWXYZ')
    [801, 1212, 1500]
    """
    return codierungBlockListe(zerlegung(wort, blocklaenge), abc)
doctest.run_docstring_examples(codierung, globals())

In [57]:
def decodierungBlockcodierung(zahl, blocklaenge, abc):
    """ 
    >>> decodierungBlockcodierung(10203, 3, ' ABCDEFGHIJKLMNOPQRSTUVWXYZ')
    'ABC'
    """
    wort = ''
    while blocklaenge > 0:
        rest = zahl % (10**2)
        wort = decodierungZahl(rest, abc) + wort
        zahl = zahl // (10**2)
        blocklaenge = blocklaenge - 1
    return wort
    
def decodierungListeBlockcodierung(zahlenListe, blocklaenge, abc):
    """ 
    >>> decodierungListeBlockcodierung([801, 1212, 1500], 2, ' ABCDEFGHIJKLMNOPQRSTUVWXYZ')
    ['HA', 'LL', 'O ']
    """
    liste = []
    for zahl in zahlenListe:
        liste = liste + [decodierungBlockcodierung(zahl, blocklaenge, abc)]
    return liste
doctest.run_docstring_examples(decodierungBlockcodierung, globals())
doctest.run_docstring_examples(decodierungListeBlockcodierung, globals())

In [58]:
def zusammenfuegung(liste):
    """ 
    >>> zusammenfuegung(['HA', 'LL', 'O '])
    'HALLO'
    """
    ergebnis = ''
    listeOhneLetztesWort = liste[:len(liste)-1]
    letztesWort = liste[len(liste)-1]
    for wort in listeOhneLetztesWort:
        ergebnis = ergebnis + wort
    # Leerzeichen am Ende entfernen
    m = len(letztesWort)-1
    gefunden = False
    while m >= 0 and not gefunden:
        c = letztesWort[m]
        if c != ' ':
            gefunden = True
        else:
            m = m-1
    letztesWort = letztesWort[0:m+1]
    ergebnis = ergebnis + letztesWort
    return ergebnis
doctest.run_docstring_examples(zusammenfuegung, globals())

In [59]:
def decodierung(zahlenListe, blocklaenge, abc):
    """ 
    >>> decodierung([801, 1212, 1500], 2, ' ABCDEFGHIJKLMNOPQRSTUVWXYZ')
    'HALLO'
    """
    return zusammenfuegung(decodierungListeBlockcodierung(zahlenListe, blocklaenge, abc))
doctest.run_docstring_examples(decodierung, globals())

# Verschlüsselung

In [60]:
def modpot(x, y, m):
    """
    >>> modpot(52, 37, 77)
    24
    """
    pot = 1
    while y > 0:
        if y % 2 == 1:
            pot = (pot * x) % m
            y = y - 1
        else:
            x = (x * x) % m
            y = y // 2
    return pot
doctest.run_docstring_examples(modpot, globals())

In [61]:
def verschluesselteZahl(zahl, schluessel):
    """
    >>> verschluesselteZahl(19, (13, 77))
    61
    """
    return modpot(zahl, schluessel[0], schluessel[1])

def verschluesselung(zahlenListe, schluessel):
    """ 
    >>> verschluesselung([1, 19, 20, 5, 18, 9, 24], (13, 77))
    [1, 61, 69, 26, 46, 58, 52]
    >>> verschluesselung([1, 61, 69, 26, 46, 58, 52], (37, 77))
    [1, 19, 20, 5, 18, 9, 24]
    """
    liste = []
    for zahl in zahlenListe:
        liste = liste + [verschluesselteZahl(zahl, schluessel)]
    return liste
doctest.run_docstring_examples(verschluesselteZahl, globals())
doctest.run_docstring_examples(verschluesselung, globals())

# Hilfsfunktionen  zu RSA

In [62]:
def egcd(a, b):
    if a == 0:
        return (b, 0, 1)
    else:
        g, y, x = egcd(b % a, a)
        return (g, x - (b // a) * y, y)

def modinv(a, m):
    """
    >>> modinv(13, 48)
    37
    >>> modinv(7911, 23140)
    3551
    """
    g, x, y = egcd(a, m)
    if g != 1:
        raise Exception('modular inverse does not exist')
    else:
        return x % m
doctest.run_docstring_examples(modinv, globals())

In [63]:
def primfaktorzerlegung(n):
    """
    >>> primfaktorzerlegung(77)
    [7, 11]
    >>> primfaktorzerlegung(23449)
    [131, 179]
    """
    faktoren = []
    d = 2  # Start mit der kleinsten Primzahl
    while d * d <= n:  # Nur bis zur Wurzel von n prüfen
        while n % d == 0:
            faktoren.append(d)
            n //= d
        d += 1
    if n > 1:
        faktoren.append(n)  # Falls noch ein Primfaktor übrig bleibt
    return faktoren
doctest.run_docstring_examples(primfaktorzerlegung, globals())

In [64]:
def rsa_keys_ok(pub, priv):
    n = pub[1]
    p = primfaktorzerlegung(n)[0]
    q = n // p
    key_ok = True
    if (pub[0]*priv[0]) % ((p-1)*(q-1)) != 1 or p*q != n:
        key_ok = False
    return key_ok

In [65]:
def rsa_calc_privat_key(p, q, e):
    """
    >>> rsa_calc_privat_key(7, 11, 13)
    (37, 77)
    """
    n = p*q
    phi = (p-1)*(q-1)
    d = modinv(e, phi)
    return ((d, n))
doctest.run_docstring_examples(rsa_calc_privat_key, globals())

In [66]:
def attack_rsa(pub):
    """
    >>> attack_rsa((13, 77))
    (37, 77)
    """
    n = pub[1]
    p = primfaktorzerlegung(n)[0]
    q = n // p
    return (modinv(pub[0], (p-1)*(q-1)), n)
doctest.run_docstring_examples(attack_rsa, globals())

# Festlegung der Schlüssel

In [67]:
oeffentlicherSchluessel = (65537, 3001122295343)
privaterSchluessel      = (2384015708753, 3001122295343)
print( rsa_keys_ok(oeffentlicherSchluessel, privaterSchluessel) )
print( attack_rsa(oeffentlicherSchluessel) )

True
(2384015708753, 3001122295343)


In [68]:
oeffentlicherSchluessel = (7911, 23449)
privaterSchluessel      = (3551, 23449)
print( rsa_keys_ok(oeffentlicherSchluessel, privaterSchluessel) )
print( attack_rsa(oeffentlicherSchluessel) )

True
(3551, 23449)


In [69]:
oeffentlicherSchluessel = (13, 77)
privaterSchluessel      = (37, 77)
print( rsa_keys_ok(oeffentlicherSchluessel, privaterSchluessel) )
print( attack_rsa(oeffentlicherSchluessel) )

True
(37, 77)


# Festlegung der Parameter

In [70]:
abc = ' ABCDEFGHIJKLMNOPQRSTUVWXYZabcdefghijklmnopqrstuvwxyzäöüßÄÖÜ.,?!😊'

In [71]:
abc = ' ABCDEFGHIJKLMNOPQRSTUVWXYZ'


In [72]:
blocklaenge=1

In [73]:
quelltext = "VIELE GRUESSE AUS GALLIEN"

In [74]:
quelltext = "NIX LOS"

In [75]:
quelltext = "Liebe Falbala, viele Grüße aus Rom, dein Obelix 😊!"

In [76]:
quelltext = "ASTERIX"

# Ausführung RSA-Verschlüsselung

In [77]:
if codierung("Z"*blocklaenge, blocklaenge, abc)[0] >= oeffentlicherSchluessel[1]:
    print("ERROR: oeffentlicher Schluessel zu klein")
    raise SystemExit
print("Blocklaenge:              ", blocklaenge)
print("Oeffentlicher Schluessel: ", oeffentlicherSchluessel)
print("Privater Schluessel:      ", privaterSchluessel)

quellcode  =  codierung(quelltext, blocklaenge, abc)
geheimcode =  verschluesselung(quellcode, oeffentlicherSchluessel)

entschluesseltercode = verschluesselung(geheimcode, privaterSchluessel)
entschluesseltertext = decodierung(entschluesseltercode, blocklaenge, abc)    

print("Quelltext:             ", quelltext)
print("Quellcode:             ", quellcode)
print("Geheimcode:            ", geheimcode)
print("Entschluesselter Code: ", entschluesseltercode)
print("Entschluesselter Text: ", entschluesseltertext)

Blocklaenge:               1
Oeffentlicher Schluessel:  (13, 77)
Privater Schluessel:       (37, 77)
Quelltext:              ASTERIX
Quellcode:              [1, 19, 20, 5, 18, 9, 24]
Geheimcode:             [1, 61, 69, 26, 46, 58, 52]
Entschluesselter Code:  [1, 19, 20, 5, 18, 9, 24]
Entschluesselter Text:  ASTERIX


 <div style="padding: 5px; border: 5px solid #0077b6;">

# Aufgabe 1

Der öffentliche Schlüssel von Alice ist (19, 65). Es wurde unsere Standardcodierung mit einer Blocklänge 1 benutzt. Mr(s). X hat folgenden Geheimcode abgefangen:

[48, 9, 60, 38, 60, 0, 58, 47, 31, 60, 59, 59, 60, 0, 1, 31, 59, 0, 58, 1, 38, 38, 9, 60, 14]

Kannst du Mr(s). X helfen, die Nachricht zu entschlüsseln? 

<div style="padding: 5px; border: 5px solid #0077b6;">

# Aufgabe 2

Der öffentliche Schlüssel von Alice ist (113, 6887). Es wurde unsere Standardcodierung mit der Blocklänge 2 benutzt. Mr(s). X hat folgenden Geheimcode abgefangen:

[6613, 5456, 1378, 2773, 1646, 5581, 4072]


Kannst du Mr(s). X helfen, die Nachricht zu entschlüsseln? Wo liegt jetzt das Problem? 

<div style="padding: 5px; border: 5px solid #0077b6;">

# Aufgabe 3

Der öffentliche Schlüssel von Alice ist (1432765433173537777777, 1914269284601333234385791628203). Es wurde unsere Standardcodierung mit der Blocklänge 15 benutzt. Mr(s). X hat folgenden Geheimcode abgefangen:

[1484723618683282017476932691981, 1335981139459882474539235587779]

Kannst du Mr(s). X helfen, die Nachricht zu entschlüsseln? Wo liegt jetzt das Problem? 

Tipp: <https://de.numberworld.info/faktorisierungsRechner>